# Ax Service API with RayTune on PyTorch CNN

Ax integrates easily with different scheduling frameworks and distributed training frameworks. In this example, Ax-driven optimization is executed in a distributed fashion using [RayTune](https://ray.readthedocs.io/en/latest/tune.html). 

RayTune is a scalable framework for hyperparameter tuning that provides many state-of-the-art hyperparameter tuning algorithms and seamlessly scales from laptop to distributed cluster with fault tolerance. RayTune leverages [Ray](https://ray.readthedocs.io/)'s Actor API to provide asynchronous parallel and distributed execution.

Ray 'Actors' are a simple and clean abstraction for replicating your Python classes across multiple workers and nodes. Each hyperparameter evaluation is asynchronously executed on a separate Ray actor and reports intermediate training progress back to RayTune. Upon reporting, RayTune then uses this information to performs actions such as early termination, re-prioritization, or checkpointing.

In [1]:
import logging
from ray import tune
from ray.tune import track
from ray.tune.suggest.ax import AxSearch
logger = logging.getLogger(tune.__name__)  
logger.setLevel(level=logging.CRITICAL)  # Reduce the number of Ray warnings that are not relevant here.

In [2]:
import torch
import numpy as np

from ax.plot.contour import plot_contour
from ax.plot.trace import optimization_trace_single_method
from ax.service.ax_client import AxClient
from ax.utils.notebook.plotting import render, init_notebook_plotting
from ax.utils.tutorials.cnn_utils import load_mnist, train, evaluate


init_notebook_plotting()

[INFO 03-20 17:06:45] ipy_plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


## 1. Initialize client
We specify `enforce_sequential_optimization` as False, because Ray runs many trials in parallel. With the sequential optimization enforcement, `AxClient` would expect the first few trials to be completed with data before generating more trials.

When high parallelism is not required, it is best to enforce sequential optimization, as it allows for achieving optimal results in fewer (but sequential) trials. In cases where parallelism is important, such as with distributed training using Ray, we choose to forego minimizing resource utilization and run more trials in parallel.

In [3]:
ax = AxClient(enforce_sequential_optimization=False)

[INFO 03-20 17:06:46] ax.service.ax_client: Starting optimization with verbose logging. To disable logging, set the `verbose_logging` argument to `False`. Note that float values in the logs are rounded to 2 decimal points.


## 2. Set up experiment
Here we set up the search space and specify the objective; refer to the Ax API tutorials for more detail.

In [4]:
ax.create_experiment(
    name="mnist_experiment",
    parameters=[
        {"name": "lr", "type": "range", "bounds": [1e-6, 0.4], "log_scale": True},
        {"name": "momentum", "type": "range", "bounds": [0.0, 1.0]},
    ],
    objective_name="mean_accuracy",
)

[INFO 03-20 17:06:46] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 5 trials, GPEI for subsequent trials]). Iterations after 5 will take longer to generate due to  model-fitting.


## 3. Define how to evaluate trials
Since we use the Ax Service API here, we evaluate the parameterizations that Ax suggests, using RayTune. The evaluation function follows its usual pattern, taking in a parameterization and outputting an objective value. For detail on evaluation functions, see [Trial Evaluation](https://ax.dev/docs/runner.html). 

In [5]:
def train_evaluate(parameterization):
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    train_loader, valid_loader, test_loader = load_mnist(data_path='~/.data')
    net = train(train_loader=train_loader, parameters=parameterization, dtype=torch.float, device=device)
    track.log(
        mean_accuracy=evaluate(
            net=net,
            data_loader=valid_loader,
            dtype=torch.float,
            device=device,
        )
    )

## 4. Run optimization
Execute the Ax optimization and trial evaluation in RayTune using [AxSearch algorithm](https://ray.readthedocs.io/en/latest/tune-searchalg.html#ax-search):

In [6]:
tune.run(
    train_evaluate, 
    num_samples=30, 
    search_alg=AxSearch(ax),  # Note that the argument here is the `AxClient`.
    verbose=0,  # Set this level to 1 to see status updates and to 2 to also see trial results.
    # To use GPU, specify: resources_per_trial={"gpu": 1}.
)

2020-03-20 17:06:46,086	WARNING services.py:586 -- setpgrp failed, processes may not be cleaned up properly: [Errno 1] Operation not permitted.


2020-03-20 17:06:46,088	INFO resource_spec.py:212 -- Starting Ray with 4.35 GiB memory available for workers and up to 2.18 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).


2020-03-20 17:06:46,446	INFO services.py:1078 -- View the Ray dashboard at localhost:8265


[INFO 03-20 17:06:47] ax.service.ax_client: Generated new trial 0 with parameters {'lr': 0.04, 'momentum': 0.39}.


[INFO 03-20 17:06:47] ax.service.ax_client: Generated new trial 1 with parameters {'lr': 0.22, 'momentum': 0.05}.


...

(pid=4433) 2020-03-20 17:07:41,194	ERROR function_runner.py:99 -- Runner Thread raised error.
(pid=4433) Traceback (most recent call last):
(pid=4433)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 93, in run
(pid=4433)     self._entrypoint()
(pid=4433)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 141, in entrypoint
(pid=4433)     return self._trainable_func(config, self._status_reporter)
(pid=4433)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 267, in _trainable_func
(pid=4433)     output = train_func(config)
(pid=4433)   File "<ipython-input-5-ff8e06f677c6>", line 4, in train_evaluate
(pid=4433) TypeError: train() missing 1 required positional argument: 'net'
(pid=4433) Exception in thread Thread-1:
(pid=4433) Traceback (most recent call last):
(pid=4433)   File "/opt/python/3.7.1/lib/python3.7/threading

(pid=4458) 2020-03-20 17:07:42,471	ERROR function_runner.py:99 -- Runner Thread raised error.
(pid=4458) Traceback (most recent call last):
(pid=4458)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 93, in run
(pid=4458)     self._entrypoint()
(pid=4458)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 141, in entrypoint
(pid=4458)     return self._trainable_func(config, self._status_reporter)
(pid=4458)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 267, in _trainable_func
(pid=4458)     output = train_func(config)
(pid=4458)   File "<ipython-input-5-ff8e06f677c6>", line 4, in train_evaluate
(pid=4458) TypeError: train() missing 1 required positional argument: 'net'
(pid=4458) Exception in thread Thread-1:
(pid=4458) Traceback (most recent call last):
(pid=4458)   File "/opt/python/3.7.1/lib/python3.7/threading

(pid=4470) 2020-03-20 17:07:45,374	ERROR function_runner.py:99 -- Runner Thread raised error.
(pid=4470) Traceback (most recent call last):
(pid=4470)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 93, in run
(pid=4470)     self._entrypoint()
(pid=4470)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 141, in entrypoint
(pid=4470)     return self._trainable_func(config, self._status_reporter)
(pid=4470)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 267, in _trainable_func
(pid=4470)     output = train_func(config)
(pid=4470)   File "<ipython-input-5-ff8e06f677c6>", line 4, in train_evaluate
(pid=4470) TypeError: train() missing 1 required positional argument: 'net'
(pid=4470) Exception in thread Thread-1:
(pid=4470) Traceback (most recent call last):
(pid=4470)   File "/opt/python/3.7.1/lib/python3.7/threading

(pid=4475) 2020-03-20 17:07:45,902	ERROR function_runner.py:99 -- Runner Thread raised error.
(pid=4475) Traceback (most recent call last):
(pid=4475)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 93, in run
(pid=4475)     self._entrypoint()
(pid=4475)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 141, in entrypoint
(pid=4475)     return self._trainable_func(config, self._status_reporter)
(pid=4475)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/function_runner.py", line 267, in _trainable_func
(pid=4475)     output = train_func(config)
(pid=4475)   File "<ipython-input-5-ff8e06f677c6>", line 4, in train_evaluate
(pid=4475) TypeError: train() missing 1 required positional argument: 'net'
(pid=4475) Exception in thread Thread-1:
(pid=4475) Traceback (most recent call last):
(pid=4475)   File "/opt/python/3.7.1/lib/python3.7/threading

TuneError: ('Trials did not complete', [train_evaluate_2e8c23b2, train_evaluate_2e8c23b3, train_evaluate_2e8c23b4, train_evaluate_2e8c23b5, train_evaluate_2e8c23b6, train_evaluate_2e8c23b7, train_evaluate_2e8c23b8, train_evaluate_2f2cbf52, train_evaluate_2f2cbf53, train_evaluate_2f2cbf54, train_evaluate_2f2cbf55, train_evaluate_329f12b6, train_evaluate_329f12b7, train_evaluate_350f1c58, train_evaluate_350f1c59, train_evaluate_36ee1d80, train_evaluate_36ee1d81, train_evaluate_397384f0, train_evaluate_397384f1, train_evaluate_3b49520a, train_evaluate_3b49520b, train_evaluate_3de456ae, train_evaluate_3de456af, train_evaluate_3fcf1b3e, train_evaluate_3fcf1b3f, train_evaluate_4250f5c6, train_evaluate_4250f5c7, train_evaluate_443be8f0, train_evaluate_443be8f1, train_evaluate_46e3346e])

## 5. Retrieve the optimization results

In [7]:
best_parameters, values = ax.get_best_parameters()
best_parameters

{'lr': 0.0035144522261298635, 'momentum': 7.346423042648887e-16}

In [8]:
means, covariances = values
means

{'mean_accuracy': 0.969666685940424}

## 6. Plot the response surface and optimization trace

In [9]:
render(
    plot_contour(
        model=ax.generation_strategy.model, param_x='lr', param_y='momentum', metric_name='mean_accuracy'
    )
)

In [10]:
# `plot_single_method` expects a 2-d array of means, because it expects to average means from multiple 
# optimization runs, so we wrap out best objectives array in another array.
best_objectives = np.array([[trial.objective_mean * 100 for trial in ax.experiment.trials.values()]])
best_objective_plot = optimization_trace_single_method(
    y=np.maximum.accumulate(best_objectives, axis=1),
    title="Model performance vs. # of iterations",
    ylabel="Accuracy",
)
render(best_objective_plot)